In [1]:
import os
import pandas as pd
import sys
sys.path.append('../')
import utils.csv as csv

In [9]:
PATH='D:\\Deutschland\\FUB\\master_thesis\\data\\gee'
INPUT_DIR = os.path.join(PATH,'validation_grid_20m_cloud10')
OUTPUT_DIR = os.path.join(PATH, 'output')
DATA_DIR = os.path.join(OUTPUT_DIR, 'validation_grid_daily_padding')

DATE_CSV = 'occurrence_val_grid.csv'
MERGE_CSV = 'merged_val_grid.csv'

date_path = os.path.join(OUTPUT_DIR, DATE_CSV)
merge_path = os.path.join(OUTPUT_DIR, MERGE_CSV)

files = os.listdir(INPUT_DIR)

1 Functions for Pandas DataFrame

In [3]:
def shuffle(df:pd.DataFrame, ref:pd.DataFrame) -> pd.DataFrame:
    """Pre-processing of each input time series data"""
    df = df[~df.index.duplicated(keep='last')]
    df = pd.merge(df, ref, how='right', on='date')
    df.drop(columns=['count','spacecraft_id', 'id'], inplace=True)
    return df

In [4]:
def zero_padding(df:pd.DataFrame) -> pd.DataFrame:
    """Padding all NaN with 0"""
    df.fillna(0,inplace=True)
    return df

In [5]:
def monthly_mean_interpolate(df:pd.DataFrame) -> pd.DataFrame:
    """Calculate mean band value in vegetation months for each year"""
    df.interpolate(method='time', inplace=True)
    mean_df = df.resample('M').mean()
    mean_df = mean_df[((mean_df.index.month >= 5) & (mean_df.index.month <=9))]
    # cols = list(mean_df.keys())
    # for col in cols:
    #     mean_df[col] = mean_df[col].fillna(mean_df.groupby(mean_df.index.month)[col].transform('mean'))
    return mean_df

In [6]:
def reshape(df:pd.DataFrame) -> pd.DataFrame:
    """Turn all combination of reflectance value and date into one row"""
    # new keys and values
    keys = list(df.keys())
    data = {'id':int(df.iat[0, -1])}
    for index, row in df.iterrows():
        date = index.strftime('%Y%m%d')
        for key in keys[:-1]:
            column = f'{date} {key}'
            data[column] = [row[key]]
    # reshape data
    return pd.DataFrame(data)

2 Count all available dates among all polygons

In [8]:
def rename_file() -> None:
    tmp_dir = os.path.join(PATH,'tmp')
    for file in files:
        if file.endswith(".csv"):
            in_path = os.path.join(INPUT_DIR, file)
            try:
                df = csv.load(in_path, 'date', True)
                df.rename(columns={'fid':'id'}, inplace=True)
                if df.empty:
                    continue
            except Exception:
                continue 
            id = int(df.iloc[0, 11])
            out_path = os.path.join(tmp_dir, f'plot_{id}.csv')
            csv.export(df, out_path, True)
rename_file()

export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_64.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_66.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_1613.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_184.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_9956.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_11574.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_11576.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_11588.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_11591.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_11592.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_11595.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_11598.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plot_11599.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\tmp\plo

In [10]:
def count_dates() -> pd.DataFrame:
    """Count all available dates among all polygons"""
    map = {}
    # read each csv file
    for file in files:
        if file.endswith(".csv"):
            in_path = os.path.join(INPUT_DIR, file)
            df = csv.load(in_path, 'date', True)
            # count date occurrence
            for index, row in df.iterrows():
                date = index.strftime('%Y%m%d')
                map[date] = map.get(date, 0) + 1
    # export output as csv
    dates = list(map.keys())
    counts = list(map.values())
    output = pd.DataFrame({'date':dates, 'count':counts})
    output.sort_values(by='date', ascending=True, inplace=True)
    csv.export(output, date_path, index=False)
    return output
count_dates()

export file D:\Deutschland\FUB\master_thesis\data\gee\output\occurrence_val_grid.csv


date  count
54   20170410  12294
109  20170420   6797
0    20170430  23401
1    20170510  23401
55   20170527   7438
..        ...    ...
108  20210901   9426
104  20210903   7438
53   20210906  23401
105  20210913   7369
106  20210923   7438

[117 rows x 2 columns]

3 Merge all data frames to one csv file

In [12]:
def merge_data_frame() -> pd.DataFrame:
    """Merge all data frames to one csv file"""
    dates = csv.load(date_path, 'date', True)
    merged = pd.DataFrame(columns=['id'])
    # add each csv file to input list as data frame
    for file in files:
        if file.endswith(".csv"):
            in_path = os.path.join(INPUT_DIR, file)
            df = csv.load(in_path, 'date', True)
            id = df.iloc[0, 11]
            merged.loc[len(merged.index)] = [id]
            # pre-process
            df = shuffle(df, dates)
            df = zero_padding(df)
            # export each new csv file
            out_path = os.path.join(DATA_DIR, file[5:])
            csv.export(df, out_path, True)
    csv.export(merged, merge_path, False)
    return merged
merge_data_frame()

export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\1.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\1000.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\10000.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\10001.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\10003.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\10005.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\10007.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\10009.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\1001.csv
export file D:\Deutschland\FUB\master_thesis\data\gee\output\validation_grid_daily_padding\10010.

id
0          1.0
1       1000.0
2      10000.0
3      10001.0
4      10003.0
...        ...
23396   9995.0
23397   9996.0
23398   9997.0
23399   9998.0
23400   9999.0

[23401 rows x 1 columns]